In [1]:
# extract the coordinates of the end points of the ski runs from the runs.geojson file
import json

In [3]:
# read the runs.geojson file
with open("runs.geojson", 'r', encoding='utf-8') as file:
    runs = json.load(file)
print('runs.geojson file read.')

runs.geojson file read.


In [4]:
items = []
mytrack = []
skiarea_name ="Síaréna Vibe Park"
#skiarea_name ="Sípark Mátraszentistván"
#skiarea_name ="Nagyvillám Sípálya Visegrád"
#skiarea_name ="Donovaly, PARK SNOW Donovaly"
#skiarea_name ="Štrbské Pleso"
# skiarea_name ="Skigebiet Stuhleck - Semmering"
# identify the end points of the ski runs depending on the types of the coordinates
for i in range(len(runs["features"])):
    print(i)
    if runs["features"][i]["properties"]["uses"][0] == "downhill":
        if len(runs["features"][i]["properties"]["skiAreas"]) != 0:
            print(runs["features"][i]["properties"]["skiAreas"][0]["properties"]["name"])
            if runs["features"][i]["properties"]["skiAreas"][0]["properties"]["name"] == skiarea_name:
                # collect the slope coordinates
                points = []
                for j in range(len(runs["features"][i]["geometry"]["coordinates"])):
                    if isinstance(runs["features"][i]["geometry"]["coordinates"][0][0], float):
                        points.append({"lat": runs["features"][i]["geometry"]["coordinates"][j][1],
                                       "lon": runs["features"][i]["geometry"]["coordinates"][j][0],
                                       "ele": runs["features"][i]["geometry"]["coordinates"][j][2]})
                    else:
                        points.append({"lat": runs["features"][i]["geometry"]["coordinates"][0][j][1],
                                       "lon": runs["features"][i]["geometry"]["coordinates"][0][j][0],
                                       "ele": runs["features"][i]["geometry"]["coordinates"][0][j][2]})
                # Append a dictionary with trackname and points keys to the tracks list
                mytrack.append({"trackname": runs["features"][i]["properties"]["name"] , "points": points})
                
# Append a dictionary with name and tracks keys to the items list
items.append({"name": skiarea_name, "tracks": mytrack})
    

0
Les Trois Vallées
1
Les Trois Vallées
2
Öjberget
3
None
4
Kope
5
Mariborsko Pohorje
6
Mariborsko Pohorje
7
Tignes - Val d'Isère
8
Zermatt - Breuil-Cervinia, Breuil-Cervinia Ski Paradise
9
Les Trois Vallées
10
11
Nylendlia skianlegg
12
13
Romme Alpin
14
Romme Alpin
15
Romme Alpin
16
None
17
Wurmstein
18
Wurmstein
19
20
Skimore Oslo
21
Villars/Gryon/Les Diablerets
22
Villars/Gryon/Les Diablerets
23
Villars/Gryon/Les Diablerets
24
Villars/Gryon/Les Diablerets
25
Villars/Gryon/Les Diablerets
26
Villars/Gryon/Les Diablerets
27
28
Villars/Gryon/Les Diablerets
29
Villars/Gryon/Les Diablerets
30
Villars/Gryon/Les Diablerets
31
Villars/Gryon/Les Diablerets
32
Villars/Gryon/Les Diablerets
33
Villars/Gryon/Les Diablerets
34
Villars/Gryon/Les Diablerets
35
Villars/Gryon/Les Diablerets
36
Villars/Gryon/Les Diablerets
37
Glomfjord Alpinsenter
38
None
39
40
41
Fridabacken
42
Pinzolo
43
44
Valdres Alpinsenter
45
46
None
47
48
Beitostølen Skisenter
49
50
51
Meråker alpinsenter
52
Meråker alpinsenter


In [9]:
# Create the JSON structure
json_data = {"items": items}
    
# save the coordinates of the starting points of the ski lifts to a json file
with open('json/slopes/raw/test.json', 'w') as file:
    json.dump(json_data, file, indent=4)

In [11]:
import json

# Load your JSON data
with open('json/slopes/raw/test.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# Iterate through the items and tracks to update tracknames
for item in data['items']:
    for i, track in enumerate(item['tracks']):
        track['trackname'] = str(i + 1)  # Set trackname to the incrementing number (starting from 1)

# Save the updated JSON back to a file
with open('json/slopes/raw/updated_json_file.json', 'w', encoding='utf-8') as f:
    json.dump(data, f, indent=4, ensure_ascii=False)

print("Track names have been updated.")


Track names have been updated.


In [2]:
import json
import gpxpy
import gpxpy.gpx

# Load the JSON data
with open('json/slopes/interpolated_ref_points.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# Create a GPX object
gpx = gpxpy.gpx.GPX()

# Iterate through the items and tracks to create GPX tracks
for item in data['items']:
    for track in item['tracks']:
        # Create a new GPX track
        gpx_track = gpxpy.gpx.GPXTrack()
        gpx.tracks.append(gpx_track)
        
        # Set the track name (from the JSON trackname)
        gpx_track.name = str(track['trackname'])
        
        # Create a GPX segment
        gpx_segment = gpxpy.gpx.GPXTrackSegment()
        gpx_track.segments.append(gpx_segment)
        
        # Iterate through the points in the track and add them to the segment
        for point in track['points']:
            gpx_segment.points.append(gpxpy.gpx.GPXTrackPoint(
                point['lat'], point['lon']
            ))

# Save the GPX data to a file
with open('output.gpx', 'w', encoding='utf-8') as f:
    f.write(gpx.to_xml())

print("GPX file has been created and saved as 'output.gpx'.")


GPX file has been created and saved as 'output.gpx'.


In [18]:
import json
import math
from itertools import combinations

# Function to calculate distance using Haversine formula
def haversine(lat1, lon1, lat2, lon2):
    R = 6371  # Earth's radius in km
    phi1, phi2 = math.radians(lat1), math.radians(lat2)
    dphi = math.radians(lat2 - lat1)
    dlambda = math.radians(lon2 - lon1)

    a = math.sin(dphi / 2)**2 + math.cos(phi1) * math.cos(phi2) * math.sin(dlambda / 2)**2
    c = 2 * math.atan2(math.sqrt(a), math.sqrt(1 - a))
    return R * c * 1000  # Convert to meters

# Function to check if points have strictly decreasing elevation
def is_elevation_decreasing(points):
    return all(points[i]['ele'] > points[i + 1]['ele'] for i in range(len(points) - 1))

# Load the input JSON
with open('Epleny_slopes.json', 'r', encoding='utf-8') as f:
    data = json.load(f)

# Output data structure
output_data = {"items": []}
max_distance = 500  # Maximum allowable distance for track combination

# Process each ski area
for item in data['items']:
    print(f"Processing ski area: {item['name']}")
    new_item = {"name": item["name"], "tracks": []}
    tracks = item["tracks"]

    # Iterate over all unique pairs of tracks
    for track1, track2 in combinations(tracks, 2):
        last_point_t1 = track1["points"][-1]
        first_point_t2 = track2["points"][0]
        distance = haversine(
            last_point_t1["lat"], last_point_t1["lon"],
            first_point_t2["lat"], first_point_t2["lon"]
        )

        # Combine points and log details
        combined_points = track1["points"] + track2["points"]
        elevations = [p['ele'] for p in combined_points]
        print(f"Evaluating {track1['trackname']} -> {track2['trackname']} | Distance: {distance:.2f}m | Elevations: {elevations}")

        if distance > max_distance:
            print(f"Skipped due to distance: {distance:.2f}m")
            continue

        if is_elevation_decreasing(combined_points):
            print(f"Valid combination: {track1['trackname']} + {track2['trackname']}")
            new_item["tracks"].append({
                "trackname": f"{track1['trackname']}+{track2['trackname']}",
                "points": combined_points
            })
        else:
            print(f"Skipped due to elevation.")

    # Retain original tracks if no combinations are valid
    if not new_item["tracks"]:
        print(f"No valid combinations for {item['name']}, retaining original tracks.")
        new_item["tracks"] = tracks

    output_data["items"].append(new_item)

# Save the output JSON
with open('valid_combinations_debugged.json', 'w', encoding='utf-8') as f:
    json.dump(output_data, f, indent=4, ensure_ascii=False)

print("Processed valid combinations saved to 'valid_combinations_debugged.json'.")


Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
Processing ski area: Síaréna Vibe Park
No valid combinations for Síaréna Vibe Park, retaining original tracks.
P

In [5]:
isinstance(runs["features"][84879]["geometry"]["coordinates"][0][0], float)

True

In [6]:
len(runs["features"][84879]["geometry"]["coordinates"])

99

In [7]:
runs["features"][84879]["geometry"]["coordinates"][5]

[10.367784400000003, 62.10768039999999, 858.06]

In [8]:
runs["features"][84879]["properties"]["skiAreas"]

[{'properties': {'activities': ['nordic'],
   'generated': True,
   'id': '18fc74e3-e603-4e6a-9e8b-0e83ae4fc8a0',
   'location': {'iso3166_1Alpha2': 'NO',
    'iso3166_2': None,
    'localized': {'en': {'country': 'Norway',
      'region': None,
      'locality': 'Alvdal'}}},
   'name': None,
   'runConvention': 'europe',
   'sources': [],
   'status': 'operating',
   'type': 'skiArea',
   'websites': [],
   'statistics': {'runs': {'byActivity': {'nordic': {'byDifficulty': {'other': {'count': 28,
         'lengthInKm': 58.37672039325018,
         'minElevation': 651.64,
         'maxElevation': 1034.93,
         'combinedElevationChange': 952.9599999999997}}}},
     'minElevation': 651.64,
     'maxElevation': 1034.93},
    'lifts': {'byType': {}},
    'maxElevation': 1034.93,
    'minElevation': 651.64}},
  'type': 'Feature',
  'geometry': {'coordinates': [10.32782796222043, 62.11510479747944],
   'type': 'Point'}}]